# Primeritat i factorització

###  Artur Travesa

#### (versió 2024-07)

# Capítol 3. Construcció certificada de nombres primers

## 3.0. Introducció

L'objectiu d'aquest capítol és aprendre a construir nombres primers de mida (en bits) prefixada, i de certificar que ho són, de primers.

Com a exemple, construirem una parella de nombres primers de $512$ bits cadascun, de manera que el seu producte serà un nombre natural d'entre $1013$ i $1024$ bits. En particular, si satisfessin algunes condicions extres, podrien formar part d'una clau RSA de $1024$ bits.

<b>Observació</b>. El sol fet de donar-los a conèixer, ja els invalida per a ser-ho de debò, de part d'una clau; però poden servir com a exemple.

### 3.0.0. Funcions que aprofitarem de capítols anteriors

En aquesta introducció, afegirem les funcions que hem programat en capítols anteriors i que seran útils per a aquest, encara que <i>SageMath</i> tingui funcions programades més eficients que les nostres. 

#### 3.0.0.0. Tests de primeritat i certificats de composició

In [ ]:
def SolovayStrassenTest(nn,ff):
    if nn==1:
        return false
    if nn in [2,3,5,7]:
        return true
    if is_even(nn):
        return false
    if ff<1:
        return 'Cal fer alguna prova.'
    f=0
    n2=(nn-1)//2
    while f<ff:
        g=ZZ.random_element(2,nn-1)
        x=Mod(g,nn)^n2
        if x==1 or x==nn-1:
            y=Mod(kronecker(g,nn),nn)
            if y!=x:
                return false
        else:
            return false
        f=f+1
    return 'Indeterminat'


In [ ]:
def MillerRabinTest(nn,ff):
    if nn==1:
        return false
    if nn in [2,3,5,7]:
        return true
    if is_even(nn):
        return false
    if ff<1:
        return 'Cal fer alguna prova.'
    v=0
    m=nn-1
    while is_even(m):
        v=v+1
        m=m//2
    f=0
    while f<ff:
        g=ZZ.random_element(2,nn-1)
        x=Mod(g,nn)^m
        if x!=1 and x!=nn-1:
            k=1
            x=x^2
            while (x!=nn-1 and k<v-1):
                x=x^2
                k=k+1
            if k>=v-1 and x!=nn-1:
                return false
        f=f+1
    return 'Indeterminat'


In [ ]:
def SolovayStrassenCert(nn,ff):
    if nn==1:
        return [nn,false,1]
    if nn==2 or nn==3:
        return [nn,true,nn-1,[nn-1]]
    if nn==5:
        return [nn,true,2,[2]]
    if nn==7:
        return [nn,true,3,[2,3]]
    if is_even(nn):
        return [nn,false,2]
    if ff<1:
        return 'Cal fer alguna prova.'
    f=0
    n2=(nn-1)//2
    while f<ff:
        g=ZZ.random_element(2,nn-1)
        x=Mod(g,nn)^n2
        if x ==1 or x==nn-1:
            y=Mod(kronecker(g,nn),nn)
            if y!=x:
                return [nn,false,g]
        else:
            return [nn,false,g]
        f=f+1
    return 'Indeterminat'


In [ ]:
def MillerRabinCert(nn,ff):
    if nn==1:
        return [nn,false,1]
    if nn==2 or nn==3:
        return [nn,true,nn-1,[nn-1]]
    if nn==5:
        return [nn,true,2,[2]]
    if nn==7:
        return [nn,true,3,[2,3]]
    if is_even(nn):
        return [nn,false,2]
    if ff<1:
        return 'Cal fer alguna prova.'
    v=0
    m=nn-1
    while is_even(m):
        v=v+1
        m=m//2
    f=0
    while f<ff:
        g=ZZ.random_element(2,nn-1)
        x=Mod(g,nn)^m
        if x!=1 and x!=nn-1:
            k=1
            x=x^2
            while (x!=nn-1 and k<v-1):
                x=x^2
                k=k+1
            if k>=v-1 and x!=nn-1:
                return [nn,false,g]
        f=f+1
    return 'Indeterminat'


#### 3.0.0.1. Certificats de primeritat

In [ ]:
def Certifica(pp,fppmu,ff):
    if pp==1:
        return [pp,false,1]
    if pp==2 or pp==3:
        return [pp,true,pp-1,[pp-1]]
    if is_even(pp):
        return [pp,false,2]
    if ff<1:
        return ["Cal fer alguna prova."]
    if len(fppmu)==0:
        lta1=factor(pp-1)
        lta=[lta1[i][0] for i in range(len(lta1))]
    else:
        lta=sorted(fppmu)
    l=len(lta)
    f=0
    while f<ff:
        g=ZZ.random_element(2,pp-2)
        if (s:=Mod(g,pp)^((pp-1)//2))==pp-1:
            i=1
            while i<= l-1 and Mod(g,pp)^((pp-1)//lta[i])!=1:
                i=i+1
            if i==l:
                return [pp,true,g,lta]
        else:
            if s!=1:
                return [pp,false,g]
        f=f+1
    return [pp,'Indeterminat']


In [ ]:
def Pocklington(pp,tt,ff):
    if not pp in ZZ or pp<1:
        return ['Cal que el nombre P sigui enter positiiu.']
    if pp==1:
        return [pp,false,1]
    if pp==2 or pp==3:
        return [pp,true,pp-1,[pp-1]]
    if is_even(pp):
        return [pp,false,2]
    if ff<1:
        return 'Cal fer alguna prova.'
# Comprovació que la llista tt és de divisors de pp-1, i càlcul de U;
# però no que són primers.
    if false in [(r in ZZ and r>1) for r in tt]:
        return 'La llista T no és de nombres enters >1.'
# Si 2 no pertany a la llista tt, li afegim (per a millora del càlcul)
    t=tt
    if not (2 in t):
        t=[2]+t
    x=prod(t)
    q,r=divmod(pp-1,x)
    if r:
        return 'La llista T no és correcta.'
    d=gcd(q,x)
    while d>1:
        q=q//d
        d=gcd(q,x)
    uu=q
    q=uu^2
    if q==pp:
        return [pp,false,uu]
    if q>pp:
        return 'U és massa gran.'
    t=sorted(t)
# Si hem arribat aquí, és que P, T, F i U són correctes (excepte,
# potser, que alguns elements de T no siguin primers).
    l=len(t)
    f=0
    while f<ff:
        g=ZZ.random_element(2,pp-2)
        if (s:=Mod(g,pp)^((pp-1)//2))==pp-1:
            i=1
            while i<= l-1 and gcd((s:=Mod(g,pp)^((pp-1)//t[i]))-1,pp)==1 and s^t[i]==1:
                i=i+1
            if i==l:
                return [pp,true,g,t]
        else:
            if s!=1:
                return [pp,false,g]
        f=f+1
    return [pp,'Indeterminat']    


## 3.1. Primers de 112 bits

<b>Observació</b>. A fi d'evitar feines feixugues i, alhora, poc eficients, suposarem que la funció is_prime( ) de <i>SageMath</i> dóna la resposta correcta per a nombres naturals menors que $2^{32}$; és a dir, de 32 o menys xifres binàries (de fet, podríem suposar això mateix per a un interval molt més gran, però ens limitarem a aquest).

D'aquesta manera, si un nombre natural n és menor que $2^{32}$ i la comanda is_prime(n) retorna True donarem el nombre n com a primer certificat. (I, de fet, el nombre és prou petit perquè la nostra funció el pugui certificar sense problemes.)

### 3.1.0. Construcció d'una primera llista de nombres primers 

Es tracta de construir una llista, que anomenarem lp112, de 10 nombres primers de 112 bits i certificar-los, però sense emmagatzemar, ni escriure, els certificats. (En farem servir 8, d'aquests nombres, però en tenim un parell més per si algun presentés problemes.)

Per a construir aquesta llista, definirem una funció Primer112( )
que calculi un nombre primer d'aquesta mida a partir d'una cerca a l'atzar entre els nombres senars de 112 bits. Un cop feta la tria, li passarem el test de Solovay-Strassen, de manera que si el nombre triat és compost, no passarà el test i en triarem un altre. Això ho farem successivament un màxim de, posem, 500 vegades. Un cop en tinguem un que passi el test (que, per tant, deu ser primer), el certificarem com a primer i el retornarem. Si no és primer o hem arribat al final sense trobar-ne cap en el nombre màxim fixat de tries, retornarem $0$.

Després, aplicarem aquesta funció per a fer una llista de 10 nombres.

In [ ]:
def Primer112():
    fita=500
    n=0
    while not SolovayStrassenCert((q:=(2*ZZ.random_element(2^110,2^111)+1)),25)[1] and n<fita:
        n=n+1
    if n<fita and Certifica(q,[],50)[1]:
        return q
    return 0


In [ ]:
lp112=[Primer112() for i in range(10)]

In [ ]:
lp112

Encara que no cal, podem veure'n certificats (que fem de nou); notem que, com que no coneixem prou primers que divideixin p-1, és més útil la funció Certifica que la funció Pocklington.

In [ ]:
[Certifica(lp112[i],[],50) for i in range(10)]

In [ ]:
[Pocklington(lp112[i],[2],50) for i in range(10)]

## 3.2. Primers de 480 bits

(a) Notem que el producte de quatre nombres de 112 bits és un nombre de (aproximadament) 448 bits. Siguin n1 el producte dels quatre primers nombres de lp112, i n2, el producte dels quatre darrers.

(b) Fixem-nos en n1 (per a n2 es procedeix de la mateixa manera). Per a tot nombre natural k1, el nombre p:=2*k1*n1+1 és senar; i el seu nombre de bits depèn d'un interval on es pot triar k1, interval que cal calcular a fi d'obtenir un nombre q1 d'una quantitat de bits desitjada a priori (òbviament, més gran que una unitat més que el nombre de bits de n1). Es demana calcular l'interval on cal triar k1 a fi que els nombres q1 siguin de $480$ bits.

(c) A partir d'un test de primeritat aplicat a valors successius de q1, obtinguts a partir de tries a l'atzar de valors de k1, obtindrem un valor que passi el test, de manera que (probablement) sigui un nombre primer. I com que el valor de k1 és prou petit per a poder-lo factoritzar, també coneixerem els divisors primers de q1-1=2*k1*n1 (els de n1, perquè l'hem construït com ho hem fet!). Això ens permetrà certificar el nombre q1 com a primer. Ara, però, podem usar la funció Pocklington, perquè n1 és més gran que l'arrel quadrada de q1; això evita factoritzar k1.

(d) Així, tenim una parella de nombres primers (amb certificats), q1 i q2, de 480 bits cadascun, i diferents, perquè els nombres q1-1 i q2-1 són divisibles per primers diferents.

#### (a)

In [ ]:
n1=prod(lp112[0:4])

In [ ]:
n2=prod(lp112[6:10])

#### (b)

In [ ]:
x11=floor(2^478/n1)+1
x12=floor((2^479-1)/n1)
x21=floor(2^478/n2)+1
x22=floor((2^479-1)/n2)

#### (c)

In [ ]:
kq1=ZZ.random_element(x11,x12)
kq2=ZZ.random_element(x21,x22)

In [ ]:
q1=2*kq1*n1+1
q2=2*kq2*n2+1

In [ ]:
print(q1,q2)

In [ ]:
SolovayStrassenTest(q1,50)

In [ ]:
SolovayStrassenTest(q2,50)

Com era d'esperar, els nombres triats a l'atzar no són primers. Caldrà repetir la cerca, i serà útil automatitzar-la. 

Ho farem un màxim de 500 vegades per a cadascun. Si no el trobem, podem repetir la cerca, o bé canviar el nombre n1 (o n2).

In [ ]:
fita=500

In [ ]:
while fita>0 and SolovayStrassenTest(q1,25)==false:
    kq1=ZZ.random_element(x11,x12)
    q1=2*kq1*n1+1
    fita=fita-1
if fita==0:
    q1=0
else:
    q1

In [ ]:
fita==0

In [ ]:
q1

In [ ]:
fita=500

In [ ]:
while fita>0 and SolovayStrassenTest(q2,25)==false:
    kq2=ZZ.random_element(x21,x22)
    q2=2*kq2*n2+1
    fita=fita-1
if fita==0:
    q2=0
else:
    q2

In [ ]:
fita==0

In [ ]:
q2

Cal certificar que els nombres q1 i q2 són primers. Com que coneixem els divisors primers de n1 i de n2, si volem fer-ho amb la funció Certifica, només cal calcular els de k1 i els de k2. I aquests són fàcils, perquè aquests nombres són prou petits per a poder-ne calcular la factorització. Donarem per certificats els factors primers d'aquests nombres (tot i que, formalment, caldria certificar-los).

Però no cal usar aquesta funció, i podem usar la funció Pocklington, perquè coneixem prou factorització (la de n1 i la de n2).

(Notem que les fites superiors dels intervals on es trien els valors de k1 i de k2 són menors que $2^{36}$.)

In [ ]:
x12<2^36, x22<2^36

Farem, doncs, dues llistes de primers, fq1 i fq2, fent la reunió de les llistes de divisors primers dels factors corresponents.

Notem que els divisors primers de n1 i de n2 són els que hem usat per a construir aquests nombres com a producte; per tant, són les llistes lp112[0:4] i lp112[6:10]. Per comoditat, els donem un nom.

In [ ]:
f0q1=lp112[0:4]
f0q2=lp112[6:10]

In [ ]:
fkq1=[factor(kq1)[i][0] for i in range(len(factor(kq1)))]
fkq2=[factor(kq2)[i][0] for i in range(len(factor(kq2)))]

In [ ]:
fq1=set([2]).union(fkq1).union(f0q1)
fq2=set([2]).union(fkq2).union(f0q2)

Ara ja podem certificar amb la funció Certifica.

In [ ]:
Certifica(q1,fq1,50)

In [ ]:
Certifica(q2,fq2,50)

Però també podem certificar amb la funció Pocklington.

In [ ]:
Pocklington(q1,f0q1,50)

In [ ]:
Pocklington(q2,f0q2,50)

#### (d)

I notem que, efectivament, els nombres primers q1 i q2 són de 480 bits.

In [ ]:
2^479<q1<2^480

In [ ]:
2^479<q2<2^480

## 3.3. Primers de 512 bits

Es tracta de repetir el procés, però en comptes de n1 i n2, fer servir q1 i q2 per a construir p1 i p2 de 512 bits. 

Caldrà veure on triem els nous valors de k, triar-los, reiterar les cerques a l'atzar, i finalment, certificar els primers obtinguts.

In [ ]:
y11=floor(2^510/q1)+1
y12=floor((2^511-1)/q1)
y21=floor(2^510/q2)+1
y22=floor((2^511-1)/q2)

In [ ]:
kp1=ZZ.random_element(y11,y12)
kp2=ZZ.random_element(y21,y22)

In [ ]:
p1=2*kp1*q1+1
p2=2*kp2*q2+1

In [ ]:
SolovayStrassenTest(p1,50),SolovayStrassenTest(p2,50)

In [ ]:
fita=1000

In [ ]:
while fita>0 and SolovayStrassenTest(p1,25)==false:
    kp1=ZZ.random_element(y11,y12)
    p1=2*kp1*q1+1
    fita=fita-1
if fita==0:
    p1=0
else:
    p1

In [ ]:
fita

In [ ]:
fita==0

In [ ]:
p1

In [ ]:
fita=1000

In [ ]:
while fita>0 and SolovayStrassenTest(p2,25)==false:
    kp2=ZZ.random_element(y21,y22)
    p2=2*kp2*q2+1
    fita=fita-1
if fita==0:
    p2=0
else:
    p2

In [ ]:
fita

In [ ]:
fita==0

In [ ]:
p2

In [ ]:
fkp1=[factor(kp1)[i][0] for i in range(len(factor(kp1)))]
fkp2=[factor(kp2)[i][0] for i in range(len(factor(kp2)))]

In [ ]:
fp1=sorted(set([2,q1]).union(fkp1))
fp2=sorted(set([2,q2]).union(fkp2))

In [ ]:
Certifica(p1,fp1,50)

In [ ]:
Certifica(p2,fp2,50)

Notem que, ara, la certificació encara és més senzilla amb la funció Pocklington, perquè per a p1 només necessitem el primer q1 i per a p2 només necessitem el primer q2.

In [ ]:
Pocklington(p1,[q1],50)

In [ ]:
Pocklington(p2,[q2],50)

## 3.4. Els valors obtinguts

In [ ]:
p1

In [ ]:
p2

En el moment de crear aquest fitxer, han aparegut els nombres primers

p1=7457155200882379719559443218324937452384310023859993451655496139902003327608193342030515279711203029222533328909967717618243921038892667313493075135726111

i

p2=11993318319225874756624727275295332613405843841164464060792461783148133591350090445241008456060941267658676459140384688920001063384871869184642203851157199

Però n'hem perdut el certificat, perquè no l'hem emmagatzemat. Per tant, difícilment podrem certificar-los!

## Fi del capítol 3